In [23]:
# TODO: You should filter data first accouring to `.csv` file.
import pandas as pd

file = "Baby_Products.csv"
df = pd.read_csv(file)

In [24]:
df

user_id parent_asin  rating      timestamp
0        AEO4M665ZOCBF7HEFRMTUDHLSB5Q  B004JU0H6O     4.0  1655859477958
1        AEO4M665ZOCBF7HEFRMTUDHLSB5Q  B082WJTFRR     5.0  1655860079499
2        AEO4M665ZOCBF7HEFRMTUDHLSB5Q  B08FZJ3YHH     4.0  1655860597696
3        AEO4M665ZOCBF7HEFRMTUDHLSB5Q  B017IQZ9OK     5.0  1655862402295
4        AEO4M665ZOCBF7HEFRMTUDHLSB5Q  B086QM7FVT     3.0  1657839829629
...                               ...         ...     ...            ...
1241078  AGMBTNN5HOKKKXINEATASO5OO35A  B098DFCNND     5.0  1659931102331
1241079  AGMBTNN5HOKKKXINEATASO5OO35A  B0775VH1HH     4.0  1659931365259
1241080  AGMBTNN5HOKKKXINEATASO5OO35A  B01INO7AGG     4.0  1659931589085
1241081  AGMBTNN5HOKKKXINEATASO5OO35A  B086Z727MT     5.0  1659931693722
1241082  AGMBTNN5HOKKKXINEATASO5OO35A  B08MWSBLCQ     5.0  1684845791986

[1241083 rows x 4 columns]

In [25]:
edge_list = []
dict_num_to_id = {} # reorder the node's id
dict_edge_to_score = {}
count = 0
for i in range(len(df)):
    row = df.iloc[i]
    user_id = row["user_id"]
    product_id = row["parent_asin"]
    edge = user_id + "|" + product_id
    edge_list.append(edge)
    dict_edge_to_score[edge] = row["rating"]
    if user_id not in dict_num_to_id:
        dict_num_to_id[user_id] = count
        count += 1
    if product_id not in dict_num_to_id:
        dict_num_to_id[product_id] = count
        count += 1

In [26]:
import json
path = "Baby_Products.jsonl"
dict_edge = {} #example: 8842281e1d1347389f2ab93d60773d4d|23310161 : One of my favorite books.
#edge_score = []
review_text = "This review, titled [title], gives the product a rating of [rating]. The reviewer stated, [text]."
with open(path) as f:
    for line in f:
        d = json.loads(line)
        edge = d["user_id"] + "|" + d["asin"]
        if d["title"] == "":
            reviewtext = review_text.replace("[title]", "Unknown Title")
        else:
            reviewtext = review_text.replace("[title]", d["title"])
        if d["rating"] == None:
            reviewtext = reviewtext.replace("[rating]", "Unknown")
        else:
            reviewtext = reviewtext.replace("[rating]", str(d["rating"]))
        if d["text"] == None:
            reviewtext = reviewtext.replace("[text]", "Unknown Text")
        else:
            reviewtext = reviewtext.replace("[text]", (d["text"]))
        dict_edge[edge] = reviewtext
        #edge_score.append(d["rating"])
            

In [27]:
import json
dict_id_to_text = {}
dictid_to_label = {}
nodes_texts = "This product, available from [store] and called [title], has an average rating of [average_rating]. Key features include [features], and according to the description, [description]. The price is [price], and additional details [details]."
with open("meta_Baby_Products.jsonl") as f:
    for line in f:
        d = json.loads(line)    
        label_list = []
        for x in d["categories"]:
            label_list.append(x)
        dictid_to_label[d["parent_asin"]] = label_list
        try:
            product_text = nodes_texts.replace("[main_category]", d["main_category"])
        except:
            product_text = product_text.replace("[store]", "Unknown main category")
        try:
            product_text = product_text.replace("[store]", d["store"])
        except:
            product_text = product_text.replace("[store]", "Unknown Store")
        if d["title"] == "":
            product_text = product_text.replace("[title]", "Unknown Title")
        else:
            product_text = product_text.replace("[title]", d["title"])
        if d["average_rating"] == None:
            product_text = product_text.replace("[average_rating]", "Unknown average_rating")
        else:
            product_text = product_text.replace("[average_rating]", str(d["average_rating"]))
        if d["features"] == []:
            product_text = product_text.replace("[features]","Unknown features")
        else:
            feature_text = ", ".join(d["features"])
            product_text = product_text.replace("[features]",feature_text)
        if d["description"] == "":
            product_text = product_text.replace("[description]", "Unknown Description")
        else:
            feature_text = ", ".join(d["description"])
            product_text = product_text.replace("[description]", feature_text)
        if d["price"] == None:
            product_text = product_text.replace("[price]", "Unknown price")
        else:
            product_text = product_text.replace("[price]", str(d["price"]))
        if d["categories"] == []:
            product_text = product_text.replace("[categories]","Unknown categories")
        else:
            feature_text = ", ".join(d["categories"])
            product_text = product_text.replace("[categories]",feature_text)
        if d["details"] == {}:
            product_text = product_text.replace("[details]","Unknown details")
        else:
            feature_text = [str(x)+str(y) for x, y in d["details"].items()]
            feature_text = ", ".join(feature_text)
            product_text = product_text.replace("[details]",feature_text)
        dict_id_to_text[d["parent_asin"]] = product_text

In [28]:
edge1 = [] 
edge2 = []  # edge1 edge2 are to generate edge_index
text_nodes = [None] * len(dict_num_to_id)
text_edges = []
edge_score = []
text_node_labels = [-1] * len(dict_num_to_id)

In [29]:
count = 0
for edge in edge_list:
    node1 = edge.split("|")[0]
    node2 = edge.split("|")[1]
    
    node1_id = int(dict_num_to_id[node1])
    node2_id = int(dict_num_to_id[node2])
    edge1.append(node1_id)
    edge2.append(node2_id)
    text_nodes[node1_id] = "reviewer"
    edge_score.append(dict_edge_to_score[edge])
    try:
        text_nodes[node2_id] = dict_id_to_text[node2]
    except:
        count += 1
    try:
        edge_text = dict_edge[edge]
        text_edges.append(edge_text)
    except:
        text_edges.append("Unknown")
    try:
        text_node_labels[node2_id] = dictid_to_label[node2]
    except:
        text_node_labels[node2_id] = -1
print(count)

0


In [30]:
len(text_nodes), len(edge1)

(186790, 1241083)

In [31]:
from torch_geometric.data import Data
import torch

In [32]:
edge_index = torch.tensor([edge1,edge2])

In [33]:
new_data = Data(
    edge_index=edge_index,
    text_nodes=text_nodes,
    text_edges=text_edges,
    text_node_labels=text_node_labels,
    edge_score=edge_score
)

In [34]:
new_data

Data(edge_index=[2, 1241083], text_nodes=[186790], text_edges=[1241083], text_node_labels=[186790], edge_score=[1241083])

In [35]:
count=0
for x in new_data.text_node_labels:
    if x == -1:
        count+=1
count

150777

In [40]:
new_data.text_nodes

['reviewer',
 'This product, available from Dream On Me and called Dream On Me 3” Square Corner Playmat, Greenguard Gold Certified, Playtime comfort, Reinforced Waterproof Vinyl Cover, Environment Safe Playmat, has an average rating of 4.7. Key features include Vinyl 10%/ Foam 90%, Made in the USA, THE SAFE CHOICE: Keeping in mind the health & safety of your baby, this playmat is not only Greenguard Gold & JPMA certified but also complies with the Federal Flammability Standard 16 CFR 1633., APPEALING COVER: The wonderful Dream On Me 3” Square Corner Playmat has a durable vinyl cover with an adorable cloud print., EASY MAINTENANCE: With a reinforced waterproof cover and binding that resists liquids & stains, the Dream On Me 3” Square Corner Playmat is super easy to clean with just mild soap and warm water., PRODUCT SPECS: Product dimensions are 38” L x 25.5” W x 3” H, with a weight of 3.5 Lbs., PRODUCT WARNINGS: The Dream On Me 3” Square Corner Playmat is intended to be used for babies 

In [41]:
import pickle
output_file_path = '../processed/baby.pkl'
with open(output_file_path, 'wb') as output_file:
    pickle.dump(new_data, output_file)

print(f"Data saved to {output_file_path}")

Data saved to ../processed/baby.pkl
